In [1]:
import numpy as np 
import pandas as pd 
import plotly as py
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True) 

In [2]:
df = pd.read_csv(r"\Users\Terence\Desktop\Coronavirus Visualizations\covid_19_data.csv")

In [3]:
df = df.rename(columns={'Country/Region':'Country'})
df = df.rename(columns={'ObservationDate':'Date'})
df.head()

SNo        Date Province/State         Country      Last Update  Confirmed  \
0    1  01/22/2020          Anhui  Mainland China  1/22/2020 17:00        1.0   
1    2  01/22/2020        Beijing  Mainland China  1/22/2020 17:00       14.0   
2    3  01/22/2020      Chongqing  Mainland China  1/22/2020 17:00        6.0   
3    4  01/22/2020         Fujian  Mainland China  1/22/2020 17:00        1.0   
4    5  01/22/2020          Gansu  Mainland China  1/22/2020 17:00        0.0   

   Deaths  Recovered  
0     0.0        0.0  
1     0.0        0.0  
2     0.0        0.0  
3     0.0        0.0  
4     0.0        0.0

In [4]:
df_countrydate = df[df['Confirmed']>0]
df_countrydate = df_countrydate.groupby(['Date','Country']).sum().reset_index()
df_countrydate

Date             Country    SNo  Confirmed  Deaths  Recovered
0      01/22/2020               Japan     36        2.0     0.0        0.0
1      01/22/2020               Macau     21        1.0     0.0        0.0
2      01/22/2020      Mainland China    373      547.0    17.0       28.0
3      01/22/2020         South Korea     38        1.0     0.0        0.0
4      01/22/2020              Taiwan     29        1.0     0.0        0.0
...           ...                 ...    ...        ...     ...        ...
11239  05/01/2020  West Bank and Gaza  20430      353.0     2.0       76.0
11240  05/01/2020      Western Sahara  20431        6.0     0.0        5.0
11241  05/01/2020               Yemen  20432        7.0     2.0        1.0
11242  05/01/2020              Zambia  20433      109.0     3.0       74.0
11243  05/01/2020            Zimbabwe  20434       40.0     4.0        5.0

[11244 rows x 6 columns]

In [5]:
df_countries = df.groupby(['Country', 'Date']).sum().reset_index().sort_values('Date', ascending=False)
df_countries = df_countries.drop_duplicates(subset = ['Country'])
df_countries = df_countries[df_countries['Confirmed']>0]

df_countries

Country        Date     SNo  Confirmed  Deaths  Recovered
2491                Cyprus  05/01/2020   20293      857.0    15.0      296.0
4179                 Haiti  05/01/2020   20322       85.0     8.0       10.0
9702                 Sudan  05/01/2020   20408      533.0    36.0       46.0
4085         Guinea-Bissau  05/01/2020   20320      257.0     1.0       19.0
7273           Netherlands  05/01/2020  102262    39989.0  4909.0      138.0
...                    ...         ...     ...        ...     ...        ...
7806             Palestine  03/09/2020    4322       22.0     0.0        0.0
10961         Vatican City  03/09/2020    4507        1.0     0.0        0.0
8298   Republic of Ireland  03/08/2020    4067       21.0     0.0        0.0
7489         North Ireland  02/28/2020    2685        1.0     0.0        0.0
0               Azerbaijan  02/28/2020    2664        1.0     0.0        0.0

[213 rows x 6 columns]

In [7]:
fig = px.choropleth(df_countrydate, 
                    locations="Country", 
                    locationmode = "country names",
                    color="Confirmed", 
                    hover_name="Country", 
                    animation_frame="Date"
                   )

fig.update_layout(
    title_text = 'Global Spread of Coronavirus',
    title_x = 0.5,
    geo=dict(
        showframe = False,
        showcoastlines = False,
    ))
    
fig.show()

In [8]:
fig = go.Figure(data=go.Choropleth(
    locations = df_countries['Country'],
    locationmode = 'country names',
    z = df_countries['Confirmed'],
    colorscale = 'Reds',
    marker_line_color = 'black',
    marker_line_width = 0.5,
))

fig.update_layout(
    title_text = 'Confirmed Cases as of March 28, 2020',
    title_x = 0.5,
    geo=dict(
        showframe = False,
        showcoastlines = False,
        projection_type = 'equirectangular'
    )
)

In [9]:
fig = px.pie(df_countries, values = 'Confirmed',names='Country', height=600)
fig.update_traces(textposition='inside', textinfo='percent+label')

fig.update_layout(
    title_x = 0.5,
    geo=dict(
        showframe = False,
        showcoastlines = False,
    ))

fig.show()

In [10]:
fig = px.treemap(df_countries, 
                 path=['Country'],
                 values = 'Confirmed',
                 names='Country',
                 height=600,
                 title='Proportion of cases',
                )

fig.show()

In [11]:
bar_data = df.groupby(['Country', 'Date'])['Confirmed', 'Deaths', 'Recovered'].sum().reset_index().sort_values('Date', ascending=True)

fig = px.bar(bar_data, x="Date", y="Confirmed", color='Country', text = 'Confirmed', orientation='v', height=600,
             title='Cases')
fig.show()

fig = px.bar(bar_data, x="Date", y="Deaths", color='Country', text = 'Deaths', orientation='v', height=600,
             title='Deaths')
fig.show()

fig = px.bar(bar_data, x="Date", y="Recovered", color='Country', text = 'Recovered', orientation='v', height=600,
             title='Recovered')
fig.show()

In [12]:
line_data = df.groupby('Date').sum().reset_index()

line_data = line_data.melt(id_vars='Date', 
                 value_vars=['Confirmed', 
                             'Recovered', 
                             'Deaths'], 
                 var_name='Ratio', 
                 value_name='Value')

fig = px.line(line_data, x="Date", y="Value", color='Ratio', 
              title='Confirmed cases, Recovered cases, and Death Over Time')
fig.show()